In [2]:
import os
import matplotlib.pyplot as plt
import numpy as np
import scipy.stats as stats
import pandas as pd
import altair
import seaborn
import folium
from folium import plugins
from IPython.display import display
RANDOM_SEED = 511
rng = np.random.default_rng(RANDOM_SEED)
seaborn.set_theme(style="darkgrid")
altair.renderers.enable('mimetype')
db_url = os.getenv('DB_URL')
%load_ext autoreload
%autoreload 2
import geopandas
import geoplot

# 1. QAing District Geometries
* us congress
* ny state senate
* ny state assembly
* nyc city council

and also:
* nyc cd (maybe)
* nyc zip code

Note: districts boundaries mostly include water areas but zip_codes don't. 
Community districts ARE so we can't do any fractional-part things accurately.

In [20]:
# sql = """
# SELECT 
#     office,
#     district as d,
#     name,
#     party,
#     boundary
# FROM representatives
# WHERE office =
#     'House'
#     --'State Senate'
#     --'State Assembly'
#     --'City Council'
# """

# sql = """
#     select 
#         zip_code as d, boundary, neighborhood_name
#     from zip_codes
#     where boundary is not null
# """

# sql = """
#     select 
#         borough_district_code as d, boundary, community_board_name
#     from community_districts
#     where boundary is not null
# """


sql = """
    select 
        uhf_code as d, boundary, uhf_name
    from uhfs
    where boundary is not null
"""


df = geopandas.GeoDataFrame.from_postgis(sql, db_url, geom_col='boundary')
# df['district'] = pd.Categorical(df['district'])
print(df.shape)
# print(df.isnull().sum())
display(df.head(3).T)

df.explore(
    legend=True,
    column='d',
    categorical=True,
    style_kwds={'stroke': False}
)

(42, 3)


0  \
d                                                       403   
boundary  MULTIPOLYGON Z (((-73.83935495462532 40.765056...   
uhf_name                               Flushing - Clearview   

                                                          1  \
d                                                       410   
boundary  MULTIPOLYGON Z (((-73.76701648957598 40.614217...   
uhf_name                                           Rockaway   

                                                          2  
d                                                       302  
boundary  POLYGON Z ((-73.93431460013473 40.824307119457...  
uhf_name               Central Harlem - Morningside Heights

# 2. Aggregate Statistics by District



For each representative (council, senate, assembly, house):
* for their district
+ for Harlem (or East Harlem alone)
+ for each borough
+ for NYC as a whole

* Population + % of total
* OTP patients + % of total + % of population + rank in city
    * by zip-code, estimated
* OTP admissions + % of total + % of population + rank in city
    * need to use admissions to compare to patients
    * can geolocate by boundary
* OTP patients / OTP admissions
* OTP enrollment (or capacity) + % of total + % of population + rank in city
    * can geolocate by boundary
* Mean travel time and fraction
    * skip for now.
* ODs + % of total + % of population + rank in city?
    * by UHF--also need to estimate.

* drug arrests?
* felony arrests?




## Pulling stats for a single district

In [134]:
district_type = 'State Senate'
district = 13

sql = f"""
    select *
    from representative_districts_report
    where (district_type = '{district_type}' and district = {district})
        or (district_type = 'Community District' and district in (110, 111))
        or (district_type = 'Borough') 
"""

district_sql = f"""
select *, (district = {district})::int as is_district
from representative_districts
where district_type = '{district_type}'
"""

geo_df = geopandas.GeoDataFrame.from_postgis(district_sql, db_url, geom_col='boundary')
map = geo_df.explore(
    column='is_district',
    categorical=True,
    style_kwds={'stroke': False}
)
display(map)

df = pd.read_sql(sql, con=db_url)
print(df.shape)
df.T

(8, 40)


0         1  \
district_type                                       Borough   Borough   
district                                                2.0       3.0   
district_name                                         Bronx  Brooklyn   
representative_name                                    None      None   
representative_party                                   None      None   
District Population, 2020                           1477278   2736038   
District Population, 2020, % of city                   16.8      31.1   
OTP Patients, 2019 estimate                          3535.0    2679.0   
OTP Patients, 2019 estimate, rank in city               1/5       2/5   
OTP Patients, 2019 estimate, % of city                 31.6      23.9   
OTP Patients per 1000 Population, 2019                  2.4       1.0   
OTP Patients per 1000 Population, 2019, rank in...      1/5       4/5   
OTP Patients per 1000 Population, 2019, % of city      35.2      14.4   
Harlem OTP Admissions of Patients in District, ...    630.0     282.0   
Harlem OTP Admissions of Patients in District, ...      2/5       4/5   
Harlem OTP Admissions of Patients in District, ...     27.0      12.1   
Opioid Burden, 2019 estimate                         6853.1    6475.0   
Opioid Burden, 2019 estimate, rank in city              1/5       2/5   
Opioid Burden, 2019 estimate, % of city                29.2      27.6   
Overdose Deaths, 2020 estimate                        535.0     422.0   
Overdose Deaths, 2020 estimate, rank in city            1/5       2/5   
Overdose Deaths, 2020 estimate, % of city              29.9      23.6   
Overdose Deaths per 100k Population, 2020 estimate     36.2      15.4   
Overdose Deaths per 100k Population, 2020 estim...      1/5       4/5   
Overdose Deaths per 100k Population, 2020 estim...     31.9      13.6   
Opioid Treatment Programs, 2019                        26.0      27.0   
Opioid Treatment Programs, 2019, rank in city           3/5       2/5   
Opioid Treatment Programs, 2019, % of city             21.1      22.0   
Patients Admitted to OTP Programs in District, ...   3358.0    2225.0   
Patients Admitted to OTP Programs in District, ...      2/5       3/5   
Patients Admitted to OTP Programs in District, ...     26.2      17.4   
OTP Capacity, 2019                                  10015.0    6850.0   
OTP Capacity, 2019, rank in city                        2/5       3/5   
OTP Capacity, 2019, % of city                          31.3      21.4   
Avg. Daily OTP Enrollment in District, 2019          9489.0    6093.0   
Avg. Daily OTP Enrollment in District, 2019, ra...      2/5       3/5   
Avg. Daily OTP Enrollment in District, 2019, % ...     32.5      20.9   
OTP Enrollment per 1000 Population, 2019                6.4       2.2   
OTP Enrollment per 1000 Population, 2019, rank ...      2/5       3/5   
OTP Enrollment per 1000 Population, 2019, % of ...     36.8      12.8   

                                                            2        3  \
district_type                                         Borough  Borough   
district                                                  1.0      4.0   
district_name                                       Manhattan   Queens   
representative_name                                      None     None   
representative_party                                     None     None   
District Population, 2020                             1685528  2409195   
District Population, 2020, % of city                     19.1     27.4   
OTP Patients, 2019 estimate                            2677.0   1752.0   
OTP Patients, 2019 estimate, rank in city                 3/5      4/5   
OTP Patients, 2019 estimate, % of city                   23.9     15.7   
OTP Patients per 1000 Population, 2019                    1.6      0.7   
OTP Patients per 1000 Population, 2019, rank in...        2/5      5/5   
OTP Patients per 1000 Population, 2019, % of city        23.4     10.7   
Harlem OTP Admissions of Pat